In [11]:
from alpaca_trade_api.stream import Stream
import alpaca_trade_api as tradeapi
import time
from numba import jit
import numpy as np 
import cupy as cp
from cupy import ndarray
import pandas as pd
import tensorflow as tf
import time
#import py_vollib.black_scholes
#import markowitzify
#pd.isnull(np.datetime64('NaT'))
#from pipeline_live.data.alpaca.factors import AverageDollarVolume
#from pipeline_live.data.alpaca.pricing import USEquityPricing

from zipline.finance import commission, slippage
from zipline.pipeline import Pipeline
from zipline.pipeline.factors import (RSI, AverageDollarVolume, BollingerBands, DailyReturns,
ExponentialWeightedMovingAverage, MACDSignal, MaxDrawdown, Returns, RollingPearson,RollingSpearman,VWAP,CustomFactor)
from zipline.pipeline.filters import AtLeastN
from zipline.api import (
    attach_pipeline,
    order_target_percent,
    pipeline_output,
    record,
    schedule_function,
    date_rules,
    time_rules
)
#note alpaca has all of the same factors as zipline
"""
from pipeline_live.data.alpaca.factors import (
    RSI,MACDSignal,VWAP,AverageDollarVolume, SimpleMovingAverage,
)
"""
#from pylivetrader.api import order_target, symbol
#import numba_scipy
#import alphalens as al
import tensorflow_probability as tfp
from tensorflow_probability import bijectors as tfb
from tensorflow_probability.python.math import psd_kernels as tfk
from sklearn.decomposition import PCA
from sklearn.preprocessing import MinMaxScaler
import matplotlib.pyplot as plt
#from prophet.plot import plot_plotly, plot_components_plotly
#from prophet import Prophet
#from tensortrade.data.cdd import CryptoDataDownload

from alpaca_trade_api.rest import TimeFrame
import polars as pl
import statistics
import sys
import time
import os
#import pyfolio as pf
from datetime import datetime, timedelta
from pytz import timezone
from alpaca_trade_api.rest_async import gather_with_concurrency, AsyncRest
from tiingo import TiingoClient
from websocket import create_connection
import simfin as sf
from simfin.names import *
#from tiingo import TiingoWebsocketClient

#hyper parameter optimization
#import keras_tuner as kt
#from tune_sklearn import TuneGridSearchCV
import optuna

from darts.models import TiDEModel, TFTModel

2024-01-18 23:58:29.347808: I tensorflow/core/util/port.cc:111] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-01-18 23:58:29.557371: E tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:9342] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-01-18 23:58:29.557470: E tensorflow/compiler/xla/stream_executor/cuda/cuda_fft.cc:609] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-01-18 23:58:29.557859: E tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:1518] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-01-18 23:58:29.633290: I tensorflow/core/platform/cpu_feature_g

In [3]:
import cudf
import cupy
from cuml.cluster import DBSCAN
from cuml.decomposition import PCA
from cuml import ExponentialSmoothing
from cuml import UMAP
#from cuml.neighbors import NearestNeighbors


In [14]:
config = {}

# To reuse the same HTTP Session across API calls (and have better performance), include a session key.
config['session'] = True

config['api_key'] = "292879b75e4ce811056b97bbbf8d72ca04e20de8"

client = TiingoClient(config)
API_KEY = "AKMLXVPKAQU1M9FWDYPZ"
API_SECRET = "oaCSrDz2Be4GYeEI8SSQGYEpdS1AiJvYOn3eUjcO"#oaCSrDz2Be4GYeEI8SSQGYEpdS1AiJvYOn3eUjcO
APCA_API_BASE_URL = "https://api.alpaca.markets"
alpaca = tradeapi.REST(API_KEY, API_SECRET, APCA_API_BASE_URL, 'v2')
api = alpaca
assets = api.list_assets()
Scalar = MinMaxScaler(feature_range=(-1,1))
pca = PCA()
index = 0
api_time_format = '%Y-%m-%dT%H:%M:%S.%f-04:00'
stocks_to_hold = 150
ws = create_connection("wss://api.tiingo.com/iex")

In [16]:
sf.set_data_dir('~/simfin_data/')

In [18]:
sf.set_api_key(api_key='7BcfsY04I70RRlaA0vtvBSSXmnvpPTxS')

In [22]:
offset = pd.DateOffset(days=60)
refresh_days = 30

refresh_days_shareprices = 10

def dat():#algo_time
  #pipeline_data = context.pipeline_data
  #all_assets = pipeline_data.index

  #longs = all_assets[pipeline_data.longs]
  #shorts = all_assets[pipeline_data.shorts]
  
  hub = sf.StockHub(market='us', offset=offset,refresh_days=refresh_days,refresh_days_shareprices=refresh_days_shareprices)
  x1 = hub.fin_signals(variant='daily')
  #x2 = hub.growth_signals(variant='daily')
  x3 = hub.val_signals(variant='daily')
  print("checkpoint 1")
  tickers = client.list_stock_tickers()

  print("tickers")
  print(tickers)

  #x4 = client.get_fundamentals_daily([tickers],startDate='2020-01-01',endDate='2020-12-31')

  x = pd.concat([x1, x3],1)

  #x.dropna(how='all').head()

  print("checkpoint 3")
  #df_signals = pd.concat(x, axis=1)

  x.dropna(how='all',axis=0,inplace=True)
  print("x")
  print(x)
  print(x.head(0))
  #x2 = sf.load_derived(market='us')
  y = hub.load_shareprices(variant='daily')
  y = y.dropna(how='all').head()
  data = pd.concat([x,y],1)
  head = data.head(0)

  print("stage 1 deployed")
  return data
data = dat()

Dataset "us-income-ttm" on disk (0 days old).
- Loading from disk ... Done!
Dataset "us-balance-ttm" on disk (0 days old).
- Loading from disk ... Done!
Dataset "us-cashflow-ttm" on disk (0 days old).
- Loading from disk ... Done!
Dataset "us-shareprices-daily" on disk (0 days old).
- Loading from disk ... Done!
Cache-file 'fin_signals-2a38bb7d.pickle' on disk (0 days old).
- Loading from disk ... Done!
Cache-file 'val_signals-739b68a6.pickle' on disk (0 days old).
- Loading from disk ... Done!
checkpoint 1
tickers
[{'ticker': '-P-H', 'exchange': 'NYSE', 'assetType': 'Stock', 'priceCurrency': 'USD', 'startDate': '', 'endDate': ''}, {'ticker': '-P-S', 'exchange': 'NYSE', 'assetType': 'Stock', 'priceCurrency': 'USD', 'startDate': '2018-08-22', 'endDate': '2023-05-05'}, {'ticker': '000001', 'exchange': 'SHE', 'assetType': 'Stock', 'priceCurrency': 'CNY', 'startDate': '2007-01-04', 'endDate': '2024-01-18'}, {'ticker': '000002', 'exchange': 'SHE', 'assetType': 'Stock', 'priceCurrency': 'CNY

/tmp/ipykernel_462131/3292010647.py:25: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat([x1, x3],1)


checkpoint 3
x
                   (Dividends + Share Buyback) / FCF  Asset Turnover  \
Ticker Date                                                            
A      2018-04-02                           0.297194        0.530697   
       2018-04-03                           0.297194        0.530697   
       2018-04-04                           0.297194        0.530697   
       2018-04-05                           0.297194        0.530697   
       2018-04-06                           0.297194        0.530697   
...                                              ...             ...   
ZYXI   2023-01-12                           1.459703        1.297076   
       2023-01-13                           1.459703        1.297076   
       2023-01-17                           1.459703        1.297076   
       2023-01-18                           1.459703        1.297076   
       2023-01-19                           1.459703        1.297076   

                   CapEx / (Depr + Amor)  Curren

/tmp/ipykernel_462131/3292010647.py:39: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  data = pd.concat([x,y],1)


stage 1 deployed


In [24]:
from cuml.preprocessing import MinMaxScaler
from cuml.decomposition import PCA

In [ ]:
from hyperimpute.plugins.imputers import Imputers

from sklearn.model_selection import train_test_split

method = "gain"

plugin = Imputers().get(method)

In [ ]:
out = plugin.fit_transform(data)

In [ ]:
from pytorch_lightning.callbacks.early_stopping import EarlyStopping

# stop training when validation loss does not decrease more than 0.05 (`min_delta`) over
# a period of 5 epochs (`patience`)
my_stopper = EarlyStopping(
    monitor="val_loss",
    patience=5,
    min_delta=0.05,
    mode='min',
)

pl_trainer_kwargs={"accelerator": "gpu", "devices": [0]}#{"callbacks": [my_stopper]

In [ ]:
from darts import TimeSeries
atrain = train.drop(['datetime','target','row_id', 'prediction_unit_id','month', 'day', 'hour', 'dayofweek', 'dayofyear', 'eic_count'],axis=1)
btrain = TimeSeries.from_values(atrain,static_covariates=county)

In [ ]:
model = TiDEModel(
    input_chunk_length=6,
    output_chunk_length=20,
    n_epochs=1,
    pl_trainer_kwargs=pl_trainer_kwargs,
)
model.fit(target,past_covariates=btrain)

In [ ]:
import torch
from ray import train, tune
from ray.tune.search.optuna import OptunaSearch


def objective(config):  # ①
    train_loader, test_loader = load_data()  # Load some data
    model = ConvNet().to("cpu")  # Create a PyTorch conv net
    optimizer = torch.optim.SGD(  # Tune the optimizer
        model.parameters(), lr=config["lr"], momentum=config["momentum"]
    )

    while True:
        train(model, optimizer, train_loader)  # Train the model
        acc = test(model, test_loader)  # Compute test accuracy
        train.report({"mean_accuracy": acc})  # Report to Tune


search_space = {"lr": tune.loguniform(1e-4, 1e-2), "momentum": tune.uniform(0.1, 0.9)}
algo = OptunaSearch()  # ②

tuner = tune.Tuner(  # ③
    objective,
    tune_config=tune.TuneConfig(
        metric="mean_accuracy",
        mode="max",
        search_alg=algo,
    ),
    run_config=train.RunConfig(
        stop={"training_iteration": 5},
    ),
    param_space=search_space,
)
results = tuner.fit()
print("Best config is:", results.get_best_result().config)

In [ ]:
from ray import tune
from ray.tune.schedulers import PopulationBasedTraining
from ray.tune.schedulers.pb2 import PB2 
pbt_scheduler = PopulationBasedTraining(
    time_attr='training_iteration',
    metric='loss',
    mode='min',
    perturbation_interval=1,
    hyperparam_mutations={
        "lr": [1e-3, 5e-4, 1e-4, 5e-5, 1e-5],
        "alpha": tune.uniform(0.0, 1.0),
    }
)
tuner = tune.Tuner(
    train_fn,
    tune_config=tune.TuneConfig(
        num_samples=4,
        scheduler=pbt_scheduler,
    ),
)
tuner.fit()

pb2_scheduler = PB2(
    time_attr='time_total_s',
    metric='mean_accuracy',
    mode='max',
    perturbation_interval=600.0,
    hyperparam_bounds={
        "lr": [1e-3, 1e-5],
        "alpha": [0.0, 1.0],
    }
)
tuner = tune.Tuner(train_fn, tune_config=tune.TuneConfig(scheduler=pb2_scheduler))
results = tuner.fit()

In [3]:
import pyjulia